In [1]:
import numpy as np
import time
import string

In [35]:
class ndoku():
    def __init__(self, n, domain='RR',order='neglex'):
        self.n = n
        ## generating symbols
        if domain == 'QQ':
            syms = QQ[reduce(lambda x,y: x+y, ['x%i,' % i for i in range(n*n)])[:-1]].gens()
        elif domain == 'RR':
            syms = RR[reduce(lambda x,y: x+y, ['x%i,' % i for i in range(n*n)])[:-1]].gens()
        elif domain == 'ZZ':
            syms = ZZ[reduce(lambda x,y: x+y, ['x%i,' % i for i in range(n*n)])[:-1]].gens()
        else:
            print('unknown domain %s' % domain)
            exit()
        
        syms = np.array([syms[n*i:n*(i+1)] for i in range(n)])
        
        ## building constraint polynomials
        col_sum_cons = np.sum(syms, axis=0)-np.sum(range(1,n+1))
        col_prd_cons = np.prod(syms, axis=0)-np.prod(range(1,n+1))
        col_cons = np.hstack([col_sum_cons, col_prd_cons])

        row_sum_cons = np.sum(syms, axis=1)-np.sum(range(1,n+1))
        row_prd_cons = np.prod(syms, axis=1)-np.prod(range(1,n+1))
        row_cons = np.hstack([row_sum_cons, row_prd_cons])

        box_sum_cons = [np.sum(a)-np.sum(range(1,n+1)) for a in np.vstack([np.hsplit(np.vsplit(syms, int(np.sqrt(n)))[i], int(np.sqrt(n))) for i in range(int(np.sqrt(n)))])]
        box_prd_cons = [np.prod(a)-np.math.factorial(n) for a in np.vstack([np.hsplit(np.vsplit(syms, int(np.sqrt(n)))[i], int(np.sqrt(n))) for i in range(int(np.sqrt(n)))])]
        box_cons = np.hstack([box_sum_cons, box_prd_cons])

        cel_cons = [np.prod([x-i for i in range(1,n+1)]) for x in syms.flatten()]

        cons = np.hstack([col_cons,row_cons,box_cons,cel_cons])

        ## defining ideal
        I = ideal(*tuple(cons),order=order) 
        
        ## computing groebner basis (take time)
        print('computing groebner basis...')
        s = time.time()
        G = I.groebner_basis()
        if order=='neglex': G = G.subs(dict(zip(syms.flatten(), syms.flatten()[::-1])))
        t = time.time()
        print(G)
        print('...done (%f sec)' % (t-s))
        
        self.cons = cons
        self.I = I
        self.symbols = syms
        self.G = G
    
    def fit(self, cond):
        ## cond is supposed to be in dict form as {x0:3, x4:2, ...}
        I = ideal(*self.G.subs(cond))
        sol = I.groebner_basis()
    
        sol = sol + [k-v for k,v in cond.items()]
        sol = dict(list(zip([t.variable() for t in sol],[(-t.coefficients()[1]) for t in sol])))
        
        self.sol = sol
        self.cond = copy(cond)
        for s in filter(lambda x: x not in cond.keys(), self.symbols.flatten()):
            self.cond[s] = '-'
        
        return sol
    
    def print_sols(self):
        print("input was: ")
        self._print_table(self.cond)
        print('')
        
        print('solution is: ')
#         tbl = copy(self.cond)
#         for k, v in self.sol.items():
#             tbl[k] = v
        self._print_table(self.sol)
        
    def _print_table(self, sol):
        for i, s in zip(range(self.n*self.n), slv.symbols.flatten()):
            print sol[s],
            if i % self.n == self.n-1: print ''

In [36]:
%%time
slv = ndoku(4, domain='QQ')

computing groebner basis...
Polynomial Sequence with 26 Polynomials in 16 Variables
...done (190.929376 sec)
CPU times: user 3min 8s, sys: 769 ms, total: 3min 9s
Wall time: 3min 10s


In [37]:
syms = slv.symbols
cond=dict([(syms[0,3], 4), (syms[1,0], 4), (syms[1,2], 2), (syms[2,1], 3), (syms[2,3], 1), (syms[3,0], 1)])
slv.fit(cond)
slv.print_sols()

input was: 
- - - 4 
4 - 2 - 
- 3 - 1 
1 - - - 

solution is: 
3 2 1 4 
4 1 2 3 
2 3 4 1 
1 4 3 2 


In [635]:
tuple(slv.G)

(-x0^3*x1^2*x2*x4 - 1/2*x0^3*x1^2*x2*x8 - 1/2*x0^3*x1^2*x4*x8 + x0^3*x1^2*x6*x8 + 1/2*x0^3*x1^2*x2*x9 - 1/2*x0^3*x1^2*x4*x9 - x0^3*x1^2*x4*x10 + 5/2*x0^3*x1^2*x2 + 15/2*x0^3*x1^2*x4 + 5*x0^3*x1*x2*x4 + 15/2*x0^2*x1^2*x2*x4 - 5/2*x0^3*x1^2*x6 + 5/2*x0^3*x1*x2*x8 + 15/4*x0^2*x1^2*x2*x8 + 5/2*x0^3*x1*x4*x8 + 15/4*x0^2*x1^2*x4*x8 - 5*x0^3*x1*x6*x8 - 15/2*x0^2*x1^2*x6*x8 - 5/2*x0^3*x1*x2*x9 - 15/4*x0^2*x1^2*x2*x9 + 5/2*x0^3*x1*x4*x9 + 15/4*x0^2*x1^2*x4*x9 + 5/2*x0^3*x1^2*x10 + 5*x0^3*x1*x4*x10 + 15/2*x0^2*x1^2*x4*x10 - 249/20*x0^3*x1^2 - 493/40*x0^3*x1*x2 - 747/40*x0^2*x1^2*x2 - 1497/40*x0^3*x1*x4 - 281/5*x0^2*x1^2*x4 - 19/5*x0^3*x2*x4 - 187/5*x0^2*x1*x2*x4 - 327/20*x0*x1^2*x2*x4 + 503/40*x0^3*x1*x6 + 757/40*x0^2*x1^2*x6 + 1/8*x0^3*x1*x8 + 1/8*x0^2*x1^2*x8 - 39/20*x0^3*x2*x8 - 749/40*x0^2*x1*x2*x8 - 163/20*x0*x1^2*x2*x8 - 39/20*x0^3*x4*x8 - 749/40*x0^2*x1*x4*x8 - 163/20*x0*x1^2*x4*x8 + 3/40*x0^2*x2*x4*x8 + 1/10*x0*x1*x2*x4*x8 + 3/20*x1^2*x2*x4*x8 + 153/40*x0^3*x6*x8 + 1499/40*x0^2*x1*x6*x8 

In [673]:
tuple(slv.G)[3]

x0^4 - 10*x0^3 + 35*x0^2 - 50*x0 + 24

In [677]:
latex(slv.G)

\left[- x_{0}^{3} x_{1}^{2} x_{2} x_{4} - \frac{1}{2} x_{0}^{3} x_{1}^{2} x_{2} x_{8} - \frac{1}{2} x_{0}^{3} x_{1}^{2} x_{4} x_{8} + x_{0}^{3} x_{1}^{2} x_{6} x_{8} + \frac{1}{2} x_{0}^{3} x_{1}^{2} x_{2} x_{9} - \frac{1}{2} x_{0}^{3} x_{1}^{2} x_{4} x_{9} -  x_{0}^{3} x_{1}^{2} x_{4} x_{10} + \frac{5}{2} x_{0}^{3} x_{1}^{2} x_{2} + \frac{15}{2} x_{0}^{3} x_{1}^{2} x_{4} + 5 x_{0}^{3} x_{1} x_{2} x_{4} + \frac{15}{2} x_{0}^{2} x_{1}^{2} x_{2} x_{4} - \frac{5}{2} x_{0}^{3} x_{1}^{2} x_{6} + \frac{5}{2} x_{0}^{3} x_{1} x_{2} x_{8} + \frac{15}{4} x_{0}^{2} x_{1}^{2} x_{2} x_{8} + \frac{5}{2} x_{0}^{3} x_{1} x_{4} x_{8} + \frac{15}{4} x_{0}^{2} x_{1}^{2} x_{4} x_{8} - 5 x_{0}^{3} x_{1} x_{6} x_{8} - \frac{15}{2} x_{0}^{2} x_{1}^{2} x_{6} x_{8} - \frac{5}{2} x_{0}^{3} x_{1} x_{2} x_{9} - \frac{15}{4} x_{0}^{2} x_{1}^{2} x_{2} x_{9} + \frac{5}{2} x_{0}^{3} x_{1} x_{4} x_{9} + \frac{15}{4} x_{0}^{2} x_{1}^{2} x_{4} x_{9} + \frac{5}{2} x_{0}^{3} x_{1}^{2} x_{10} + 5 x_{0}^{3} x_{1} x_{4} x_{1

In [26]:
slv.sol

{x15: 2,
 x14: 3,
 x13: 4,
 x12: 1,
 x11: 1,
 x10: 4,
 x9: 3,
 x8: 2,
 x7: 3,
 x6: 2,
 x5: 1,
 x4: 4,
 x3: 4,
 x2: 1,
 x1: 2,
 x0: 3}